# Midproject: Find the next Hype!?
Team: Sammy and Meron

### Goal

In this project we will ....

Importing all necessary libraries and reading the data

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import datetime
pd.set_option('display.max_columns', None) # displays all columns in dfs

import warnings
warnings.filterwarnings('ignore')

In [2]:
stockx = pd.read_excel("midprojectfinal.xlsx")
stockx.head(2)

Order Date   Brand                                 Sneaker Name  Sale Price  \
0 2017-09-01   Yeezy         Adidas-Yeezy-Boost-350-Low-V2-Beluga      1097.0   
1 2017-09-01   Yeezy  Adidas-Yeezy-Boost-350-V2-Core-Black-Copper       685.0   

   Retail Price Release Date  Shoe Size Buyer Region  
0           220   2016-09-24       11.0   California  
1           220   2016-11-23       11.0   California

In [3]:
stockx.rename(columns=lambda col: col.replace(' ', '_').lower(), inplace=True)

In [4]:
#We decided not to separate the color from the model as it is an indespensable part of the model

stockx["sneaker_name"].value_counts()

adidas-Yeezy-Boost-350-V2-Butter                     11423
Adidas-Yeezy-Boost-350-V2-Beluga-2pt0                10395
Adidas-Yeezy-Boost-350-V2-Zebra                      10110
Adidas-Yeezy-Boost-350-V2-Blue-Tint                   9297
Adidas-Yeezy-Boost-350-V2-Cream-White                 9097
Adidas-Yeezy-Boost-350-V2-Sesame                      5553
adidas-Yeezy-Boost-350-V2-Static                      4983
Adidas-Yeezy-Boost-350-V2-Semi-Frozen-Yellow          4854
Air-Jordan-1-Retro-High-Off-White-University-Blue     4635
adidas-Yeezy-Boost-350-V2-Static-Reflective           3184
Nike-Air-Presto-Off-White-Black-2018                  1884
Nike-Air-Presto-Off-White-White-2018                  1883
Nike-Air-VaporMax-Off-White-2018                      1591
Nike-Blazer-Mid-Off-White-All-Hallows-Eve             1435
Nike-Blazer-Mid-Off-White-Grim-Reaper                 1398
Nike-Zoom-Fly-Off-White-Pink                          1359
Nike-Air-VaporMax-Off-White-Black                     13

In [5]:
#Cleaning up dataset and removing all blanks from brand
stockx["brand"] = stockx["brand"].apply(lambda x: x.strip())
stockx.head(2) 

order_date  brand                                 sneaker_name  sale_price  \
0 2017-09-01  Yeezy         Adidas-Yeezy-Boost-350-Low-V2-Beluga      1097.0   
1 2017-09-01  Yeezy  Adidas-Yeezy-Boost-350-V2-Core-Black-Copper       685.0   

   retail_price release_date  shoe_size buyer_region  
0           220   2016-09-24       11.0   California  
1           220   2016-11-23       11.0   California

In [6]:
#Cleaning up dataset and creating identical naming 
stockx["sneaker_name"] = stockx["sneaker_name"].str.replace("adidas","Adidas")

In [7]:
stockx.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 99956 entries, 0 to 99955
Data columns (total 8 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   order_date    99956 non-null  datetime64[ns]
 1   brand         99956 non-null  object        
 2   sneaker_name  99956 non-null  object        
 3   sale_price    99956 non-null  float64       
 4   retail_price  99956 non-null  int64         
 5   release_date  99956 non-null  datetime64[ns]
 6   shoe_size     99956 non-null  float64       
 7   buyer_region  99956 non-null  object        
dtypes: datetime64[ns](2), float64(2), int64(1), object(3)
memory usage: 6.1+ MB


In [8]:
#Dimensions of the dataset
stockx.shape

(99956, 8)

In [9]:
stockx["brand"].value_counts()

Yeezy        72162
Off-White    27794
Name: brand, dtype: int64

##### Checking for Nans

In [10]:
stockx.isna().sum()

order_date      0
brand           0
sneaker_name    0
sale_price      0
retail_price    0
release_date    0
shoe_size       0
buyer_region    0
dtype: int64

Dataset has no nan values.

### Feature Engineering

#### Price Ratio

In [11]:
stockx["price_ratio"] = (stockx["sale_price"]/stockx["retail_price"]).round(2)
stockx.head(2)

order_date  brand                                 sneaker_name  sale_price  \
0 2017-09-01  Yeezy         Adidas-Yeezy-Boost-350-Low-V2-Beluga      1097.0   
1 2017-09-01  Yeezy  Adidas-Yeezy-Boost-350-V2-Core-Black-Copper       685.0   

   retail_price release_date  shoe_size buyer_region  price_ratio  
0           220   2016-09-24       11.0   California         4.99  
1           220   2016-11-23       11.0   California         3.11

#### Time Since Release

In [12]:
stockx["time_since_release"] = (stockx["order_date"]-stockx["release_date"]).dt.days.astype("int64")
stockx.head(2)

order_date  brand                                 sneaker_name  sale_price  \
0 2017-09-01  Yeezy         Adidas-Yeezy-Boost-350-Low-V2-Beluga      1097.0   
1 2017-09-01  Yeezy  Adidas-Yeezy-Boost-350-V2-Core-Black-Copper       685.0   

   retail_price release_date  shoe_size buyer_region  price_ratio  \
0           220   2016-09-24       11.0   California         4.99   
1           220   2016-11-23       11.0   California         3.11   

   time_since_release  
0                 342  
1                 282

model_names = ["Jordan","V2","airmax90","airmax97","zoom","presto","airforce","blazer","vapormax"]

for i in model_names:
    stockx[i] = stockx["sneaker_name"].apply(lambda x : 1 if "i" in x.split("-") else 0)
    
stockx

#Defining a function for extracting the features models, color and x from the column "sneaker_name"

def feature_addition(properties):
    for i in properties:
          stockx[i] = stockx["sneaker_name"].apply(lambda x : 1 if "i" in x.split("-") else 0)
    return i

#### Sneaker 

#how to account for v2 vs 350v2
model_names = ["Jordan","V2","airmax90","airmax97","zoom","presto","airforce","blazer","vapormax"]

stockx["model_names"] = stockx.apply(lambda x: feature_addition(model_names), axis=1) 

In [13]:
stockx.head(2)

order_date  brand                                 sneaker_name  sale_price  \
0 2017-09-01  Yeezy         Adidas-Yeezy-Boost-350-Low-V2-Beluga      1097.0   
1 2017-09-01  Yeezy  Adidas-Yeezy-Boost-350-V2-Core-Black-Copper       685.0   

   retail_price release_date  shoe_size buyer_region  price_ratio  \
0           220   2016-09-24       11.0   California         4.99   
1           220   2016-11-23       11.0   California         3.11   

   time_since_release  
0                 342  
1                 282

#### Colorway

colorway = ["Black"] #need to white colorway

stockx["colorway"] = stockx.apply(lambda x: feature_addition(colorway), axis=1) 

In [14]:
#colorway = ["Black"] #need to white colorway

#for i in colorway:
    #stockx[i] = stockx["sneaker_name"].apply(lambda x : 1 if "i" in x.split("-") else 0)

stockx.head(2) #black is not show yet??!

#### Feature Engineering: Colorway, State and Model

#### Model

In [15]:
#Jordan Feature
stockx["jordan"] = stockx["sneaker_name"].apply(lambda x : 1 if 'Jordan' in x.split("-") else 0)

#v2 Feature
stockx["V2"] = stockx["sneaker_name"].apply(lambda x : 1 if 'V2' in x.split("-") else 0)

#Airmax90 Feature
stockx["airmax90"] = stockx["sneaker_name"].apply(lambda x : 1 if '90' in x.split("-") else 0)

#Airmax97 Feature
stockx["airmax97"] = stockx["sneaker_name"].apply(lambda x : 1 if '97' in x.split("-") else 0)

#Air Zoom Feature
stockx["zoom"] = stockx["sneaker_name"].apply(lambda x : 1 if 'Zoom' in x.split("-") else 0)

#Presto Feature
stockx["presto"] = stockx["sneaker_name"].apply(lambda x : 1 if 'Presto' in x.split("-") else 0)

#Airforce Feature
stockx["airforce"] = stockx["sneaker_name"].apply(lambda x : 1 if 'Force' in x.split("-") else 0)

#Blazer Feature
stockx["blazer"] = stockx["sneaker_name"].apply(lambda x : 1 if 'Blazer' in x.split("-") else 0)

#Vapormax Feature
stockx["vapormax"] = stockx["sneaker_name"].apply(lambda x : 1 if 'VaporMax' in x.split("-") else 0)

#### State

In [16]:
#We take every state above 5percent, rest goes to other

#California Feature
stockx["california"] = stockx["buyer_region"].apply(lambda x : 1 if 'California' in x else 0)

#New York Feature
stockx["new_york"] = stockx["buyer_region"].apply(lambda x : 1 if 'New York' in x else 0)

#Oregon Feauture
stockx["oregon"] = stockx["buyer_region"].apply(lambda x : 1 if 'Oregon' in x else 0)

#Florida Feature
stockx["florida"] = stockx["buyer_region"].apply(lambda x : 1 if 'Florida' in x else 0)

#Texas Feature
stockx["texas"] = stockx["buyer_region"].apply(lambda x : 1 if 'Texas' in x else 0)

#Other Feature
stockx["other"] = stockx["buyer_region"].apply(lambda x : 1 if not ('Texas' or "Florida" or "Oregon" or "New York" or "California") in x else 0)

In [17]:
stockx["buyer_region"].value_counts()/len(stockx)

California              0.193575
New York                0.165323
Oregon                  0.076844
Florida                 0.063788
Texas                   0.058786
New Jersey              0.047221
Illinois                0.037837
Pennsylvania            0.031104
Massachusetts           0.029043
Michigan                0.027632
Virginia                0.020589
Ohio                    0.018908
Maryland                0.018708
Washington              0.018638
Georgia                 0.018468
Arizona                 0.013986
North Carolina          0.013446
Delaware                0.012425
Connecticut             0.011105
Indiana                 0.010265
Colorado                0.009544
Wisconsin               0.008404
Nevada                  0.007903
Tennessee               0.007313
Minnesota               0.007253
Missouri                0.006603
South Carolina          0.005703
Louisiana               0.005372
Kentucky                0.004882
Iowa                    0.004602
Alabama   

#### Colorway

In [18]:
#Black Feature
stockx["black"] = stockx["sneaker_name"].apply(lambda x : 1 if 'Black' in x else 0)

In [19]:
stockx.head(2)

order_date  brand                                 sneaker_name  sale_price  \
0 2017-09-01  Yeezy         Adidas-Yeezy-Boost-350-Low-V2-Beluga      1097.0   
1 2017-09-01  Yeezy  Adidas-Yeezy-Boost-350-V2-Core-Black-Copper       685.0   

   retail_price release_date  shoe_size buyer_region  price_ratio  \
0           220   2016-09-24       11.0   California         4.99   
1           220   2016-11-23       11.0   California         3.11   

   time_since_release  jordan  V2  airmax90  airmax97  zoom  presto  airforce  \
0                 342       0   1         0         0     0       0         0   
1                 282       0   1         0         0     0       0         0   

   blazer  vapormax  california  new_york  oregon  florida  texas  other  \
0       0         0           1         0       0        0      0      1   
1       0         0           1         0       0        0      0      1   

   black  
0      0  
1      1

We drop certain columns because we have identificators for it already

In [20]:
stockx_model = stockx.drop(["order_date","sneaker_name","sale_price","retail_price","release_date","buyer_region","time_since_release"], axis=1)

In [21]:
stockx_model.head(5)

brand  shoe_size  price_ratio  jordan  V2  airmax90  airmax97  zoom  \
0  Yeezy       11.0         4.99       0   1         0         0     0   
1  Yeezy       11.0         3.11       0   1         0         0     0   
2  Yeezy       11.0         3.14       0   1         0         0     0   
3  Yeezy       11.5         4.89       0   1         0         0     0   
4  Yeezy       11.0         3.76       0   1         0         0     0   

   presto  airforce  blazer  vapormax  california  new_york  oregon  florida  \
0       0         0       0         0           1         0       0        0   
1       0         0       0         0           1         0       0        0   
2       0         0       0         0           1         0       0        0   
3       0         0       0         0           0         0       0        0   
4       0         0       0         0           0         0       0        0   

   texas  other  black  
0      0      1      0  
1      0      1      1  
2      0      1      1  
3      0      1      1  
4      0      1      1

### EDA: Visualization and Descriptive Statistics 

In [22]:
stockx_num = stockx.select_dtypes(include=np.number)

In [23]:
stockx_cat = stockx.select_dtypes(include=np.object)
stockx_cat

brand                                   sneaker_name  buyer_region
0      Yeezy           Adidas-Yeezy-Boost-350-Low-V2-Beluga    California
1      Yeezy    Adidas-Yeezy-Boost-350-V2-Core-Black-Copper    California
2      Yeezy     Adidas-Yeezy-Boost-350-V2-Core-Black-Green    California
3      Yeezy       Adidas-Yeezy-Boost-350-V2-Core-Black-Red      Kentucky
4      Yeezy  Adidas-Yeezy-Boost-350-V2-Core-Black-Red-2017  Rhode Island
...      ...                                            ...           ...
99951  Yeezy    Adidas-Yeezy-Boost-350-V2-Static-Reflective        Oregon
99952  Yeezy    Adidas-Yeezy-Boost-350-V2-Static-Reflective    California
99953  Yeezy    Adidas-Yeezy-Boost-350-V2-Static-Reflective      New York
99954  Yeezy    Adidas-Yeezy-Boost-350-V2-Static-Reflective    California
99955  Yeezy    Adidas-Yeezy-Boost-350-V2-Static-Reflective         Texas

[99956 rows x 3 columns]

In [24]:
stockx.describe().round(1)

sale_price  retail_price  shoe_size  price_ratio  time_since_release  \
count     99956.0       99956.0    99956.0      99956.0             99956.0   
mean        446.6         208.6        9.3          2.2               183.7   
std         256.0          25.2        2.3          1.5               232.4   
min         186.0         130.0        3.5          0.8               -69.0   
25%         275.0         220.0        8.0          1.3                10.0   
50%         370.0         220.0        9.5          1.7                56.0   
75%         540.0         220.0       11.0          2.6               345.0   
max        4050.0         250.0       17.0         21.3              1321.0   

        jordan       V2  airmax90  airmax97     zoom   presto  airforce  \
count  99956.0  99956.0   99956.0   99956.0  99956.0  99956.0   99956.0   
mean       0.1      0.7       0.0       0.0      0.0      0.0       0.0   
std        0.2      0.5       0.1       0.1      0.2      0.2       0.2   
min        0.0      0.0       0.0       0.0      0.0      0.0       0.0   
25%        0.0      0.0       0.0       0.0      0.0      0.0       0.0   
50%        0.0      1.0       0.0       0.0      0.0      0.0       0.0   
75%        0.0      1.0       0.0       0.0      0.0      0.0       0.0   
max        1.0      1.0       1.0       1.0      1.0      1.0       1.0   

        blazer  vapormax  california  new_york   oregon  florida    texas  \
count  99956.0   99956.0     99956.0   99956.0  99956.0  99956.0  99956.0   
mean       0.0       0.0         0.2       0.2      0.1      0.1      0.1   
std        0.2       0.2         0.4       0.4      0.3      0.2      0.2   
min        0.0       0.0         0.0       0.0      0.0      0.0      0.0   
25%        0.0       0.0         0.0       0.0      0.0      0.0      0.0   
50%        0.0       0.0         0.0       0.0      0.0      0.0      0.0   
75%        0.0       0.0         0.0       0.0      0.0      0.0      0.0   
max        1.0       1.0         1.0       1.0      1.0      1.0      1.0   

         other    black  
count  99956.0  99956.0  
mean       0.9      0.1  
std        0.2      0.3  
min        0.0      0.0  
25%        1.0      0.0  
50%        1.0      0.0  
75%        1.0      0.0  
max        1.0      1.0

In [25]:
#Correlations

In [26]:
stockx_model.corr(method='pearson')

shoe_size  price_ratio    jordan        V2  airmax90  airmax97  \
shoe_size     1.000000     0.082965  0.015092 -0.075669  0.038257  0.036167   
price_ratio   0.082965     1.000000  0.513944 -0.667218  0.139521  0.122780   
jordan        0.015092     0.513944  1.000000 -0.391907 -0.035130 -0.029232   
V2           -0.075669    -0.667218 -0.391907  1.000000 -0.227540 -0.189339   
airmax90      0.038257     0.139521 -0.035130 -0.227540  1.000000 -0.016972   
airmax97      0.036167     0.122780 -0.029232 -0.189339 -0.016972  1.000000   
zoom          0.032316    -0.058952 -0.052261 -0.338495 -0.030342 -0.025248   
presto        0.017453     0.352587 -0.052551 -0.340376 -0.030511 -0.025389   
airforce      0.009827     0.079144 -0.039284 -0.254445 -0.022808 -0.018979   
blazer        0.017474     0.307106 -0.047697 -0.308933 -0.027693 -0.023043   
vapormax      0.015025     0.042215 -0.046362 -0.300288 -0.026918 -0.022399   
california   -0.033256     0.061673  0.020419 -0.050426  0.001490  0.024967   
new_york     -0.052401    -0.007920 -0.011476  0.009104 -0.008527 -0.002788   
oregon       -0.145723     0.028944  0.063604 -0.009697  0.022400 -0.015055   
florida       0.038275     0.001294 -0.010728 -0.011824  0.000746  0.001120   
texas         0.043572    -0.028858 -0.029019  0.020747  0.005332 -0.000301   
other        -0.043572     0.028858  0.029019 -0.020747 -0.005332  0.000301   
black         0.040780     0.210449 -0.080017 -0.343572  0.128980  0.045215   

                 zoom    presto  airforce    blazer  vapormax  california  \
shoe_size    0.032316  0.017453  0.009827  0.017474  0.015025   -0.033256   
price_ratio -0.058952  0.352587  0.079144  0.307106  0.042215    0.061673   
jordan      -0.052261 -0.052551 -0.039284 -0.047697 -0.046362    0.020419   
V2          -0.338495 -0.340376 -0.254445 -0.308933 -0.300288   -0.050426   
airmax90    -0.030342 -0.030511 -0.022808 -0.027693 -0.026918    0.001490   
airmax97    -0.025248 -0.025389 -0.018979 -0.023043 -0.022399    0.024967   
zoom         1.000000 -0.045389 -0.033930 -0.041196 -0.040044    0.005273   
presto      -0.045389  1.000000 -0.034119 -0.041425 -0.040266    0.018024   
airforce    -0.033930 -0.034119  1.000000 -0.030967 -0.030101    0.013784   
blazer      -0.041196 -0.041425 -0.030967  1.000000 -0.036546    0.020984   
vapormax    -0.040044 -0.040266 -0.030101 -0.036546  1.000000    0.012970   
california   0.005273  0.018024  0.013784  0.020984  0.012970    1.000000   
new_york    -0.006319  0.000883 -0.006570  0.002335  0.007710   -0.218047   
oregon      -0.036907 -0.000601  0.027006  0.003954 -0.040139   -0.141355   
florida      0.020265  0.010959  0.004054 -0.001104  0.001860   -0.127887   
texas        0.009252 -0.008011 -0.005501 -0.010907 -0.001537   -0.122443   
other       -0.009252  0.008011  0.005501  0.010907  0.001537    0.122443   
black        0.243237  0.244106  0.157696 -0.063076  0.184024    0.034298   

             new_york    oregon   florida     texas     other     black  
shoe_size   -0.052401 -0.145723  0.038275  0.043572 -0.043572  0.040780  
price_ratio -0.007920  0.028944  0.001294 -0.028858  0.028858  0.210449  
jordan      -0.011476  0.063604 -0.010728 -0.029019  0.029019 -0.080017  
V2           0.009104 -0.009697 -0.011824  0.020747 -0.020747 -0.343572  
airmax90    -0.008527  0.022400  0.000746  0.005332 -0.005332  0.128980  
airmax97    -0.002788 -0.015055  0.001120 -0.000301  0.000301  0.045215  
zoom        -0.006319 -0.036907  0.020265  0.009252 -0.009252  0.243237  
presto       0.000883 -0.000601  0.010959 -0.008011  0.008011  0.244106  
airforce    -0.006570  0.027006  0.004054 -0.005501  0.005501  0.157696  
blazer       0.002335  0.003954 -0.001104 -0.010907  0.010907 -0.063076  
vapormax     0.007710 -0.040139  0.001860 -0.001537  0.001537  0.184024  
california  -0.218047 -0.141355 -0.127887 -0.122443  0.122443  0.034298  
new_york     1.000000 -0.128403 -0.116169 -0.111224  0.111224 -0.002500  
oregon     

#### Plotting the target variable

In [31]:
px.histogram(stockx, x="price_ratio", title="Distribution of sneaker prices")

#sneaker prices are positively skewed

In [30]:
px.box(stockx, x="price_ratio", title="Boxplot of sneaker prices")



In [33]:
px.histogram(stockx,x="price_ratio", y="brand")

In [ ]:
#stockx.corr()

In [ ]:
plt.scatter(data['ic2'], data['ic3'])

In [ ]:
sns.boxplot(x="", data=data

In [41]:
method = ["pearson","spearman",]

def correlation(method):
    stock.corr()
    return corr

stockx.corr()#method='pearson')

sale_price  retail_price  shoe_size  price_ratio  \
sale_price            1.000000     -0.361549   0.082795     0.960253   
retail_price         -0.361549      1.000000  -0.052798    -0.588690   
shoe_size             0.082795     -0.052798   1.000000     0.082965   
price_ratio           0.960253     -0.588690   0.082965     1.000000   
time_since_release   -0.086407      0.245391   0.017450    -0.134598   
jordan                0.556765     -0.181692   0.015092     0.513944   
V2                   -0.566434      0.719892  -0.075669    -0.667218   
airmax90              0.083067     -0.275510   0.038257     0.139521   
airmax97              0.128442     -0.087779   0.036167     0.122780   
zoom                 -0.100489     -0.249324   0.032316    -0.058952   
presto                0.259918     -0.412134   0.017453     0.352587   
airforce              0.038078     -0.246293   0.009827     0.079144   
blazer                0.118352     -0.604900   0.017474     0.307106   
vapormax              0.147161      0.309541   0.015025     0.042215   
california            0.060507     -0.034841  -0.033256     0.061673   
new_york             -0.006724      0.009256  -0.052401    -0.007920   
oregon                0.025829     -0.028307  -0.145723     0.028944   
florida              -0.001233     -0.010982   0.038275     0.001294   
texas                -0.028689      0.016062   0.043572    -0.028858   
other                 0.028689     -0.016062  -0.043572     0.028858   
black                 0.214348     -0.193082   0.040780     0.210449   

                    time_since_release    jordan        V2  airmax90  \
sale_price                   -0.086407  0.556765 -0.566434  0.083067   
retail_price                  0.245391 -0.181692  0.719892 -0.275510   
shoe_size                     0.017450  0.015092 -0.075669  0.038257   
price_ratio                  -0.134598  0.513944 -0.667218  0.139521   
time_since_release            1.000000 -0.134647  0.297042 -0.083015   
jordan                       -0.134647  1.000000 -0.391907 -0.035130   
V2                            0.297042 -0.391907  1.000000 -0.227540   
airmax90                     -0.083015 -0.035130 -0.227540  1.000000   
airmax97                     -0.057282 -0.029232 -0.189339 -0.016972   
zoom                         -0.118693 -0.052261 -0.338495 -0.030342   
presto                       -0.111752 -0.052551 -0.340376 -0.030511   
airforce                     -0.102679 -0.039284 -0.254445 -0.022808   
blazer                       -0.111591 -0.047697 -0.308933 -0.027693   
vapormax                     -0.076988 -0.046362 -0.300288 -0.026918   
california                   -0.023272  0.020419 -0.050426  0.001490   
new_york                      0.014921 -0.011476  0.009104 -0.008527   
oregon                       -0.067624  0.063604 -0.009697  0.022400   
florida                       0.013591 -0.010728 -0.011824  0.000746   
texas                         0.017382 -0.029019  0.020747  0.005332   
other                        -0.017382  0.029019 -0.020747 -0.005332   
black                        -0.008032 -0.080017 -0.343572  0.128980   

                    airmax97      zoom    presto  airforce    blazer  \
sale_price          0.128442 -0.100489  0.259918  0.038078  0.118352   
retail_price       -0.087779 -0.249324 -0.412134 -0.246293 -0.604900   
shoe_size           0.036167  0.032316  0.017453  0.009827  0.017474   
price_ratio         0.122780 -0.058952  0.352587  0.079144  0.307106   
time_since_release -0.057282 -0.118693 -0.111752 -0.102679 -0.111591   
jordan             -0.029232 -0.052261 -0.052551 -0.039284 -0.047697   
V2                 -0.189339 -0.338495 -0.340376 -0.254445 -0.308933   
airmax90           -0.016972 -0.030342 -0.030511 -0.022808 -0.027693   
airmax97            1.000000 -0.025248 -0.025389 -0.018979 -0.023043   
zoom               -0.025248  1.000000 -0.045389 -0.033930 -0.041196   
presto             -0.025389 -0.045389  1.000000 -0.034119

#### Preprocessing

In [36]:
from sklearn.model_selection import train_test_split

X = stockx_model.drop("price_ratio", axis=1)
y = stockx_model["price_ratio"]

In [40]:
X_train, X_test, y_train, y_test = train_test_split(X,y, test_size= 0.2, random_state=0)

### Lasso Regression

We use lasso regerssion for identifiy the best possible features which we will later use in building our model

In [ ]:
X_test

### Linear Models

#### Linear Regression

In [ ]:
y_pred_train = regressor.predict(X_train)
y_pred_train

In [ ]:
y_pred_test = regressor.predict(X_test)
y_pred_test

In [ ]:
Validation

In [ ]:
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import r2_score

In [ ]:
print("--- Performances of the model ---")
print("the r2 score on train  :", regressor.score(X_train, y_train))
print("the r2 score on test  :", regressor.score(X_test, y_test))

In [ ]:
y_pred = regressor.predict(X)

In [ ]:
r2 = r2_score(y, y_pred)
mse = mean_squared_error(y, y_pred, squared=True)
rmse = mean_squared_error(y, y_pred, squared=False)
mae = mean_absolute_error(y, y_pred)

print("R2_score:", r2)
print("MSE:", mse)
print("RMSE:", rmse)
print("MAE:", mae)

In [ ]:
4.3 Function for Various Models

In [ ]:
from sklearn.linear_model import Ridge, Lasso
from sklearn.preprocessing import StandardScaler, PolynomialFeatures
from sklearn.neighbors import KNeighborsRegressor
from sklearn.neural_network import MLPRegressor
from sklearn.model_selection import GridSearchCV #in case we want to find Lasso's optimal alpha
import matplotlib.pyplot as plt
import seaborn as sns

In [ ]:
def model_application_and_evaluation(scaler, model, X_train, X_test, y_train, y_test):
    X_train = scaler.fit_transform(X_train)
    X_test = scaler.transform(X_test)
    model.fit(X_train,y_train)
    print("score on train set:", model.score(X_train, y_train))
    print("score on test set:", model.score(X_test, y_test))

In [ ]:
#defining different scalers
scaler1 = StandardScaler()
scaler2 = MinMaxScaler()
scaler3 = PolynomialFeatures(degree=2, interaction_only=True)

In [ ]:
#defining different models
baseline_regression = LinearRegression()
ridge = Ridge(alpha=0.3) #L2 regularizer #hyperparameters
lasso = Lasso (alpha=0.1) #L1 regularizer
knn = KNeighborsRegressor(n_neighbors=3)
mlp = MLPRegressor(random_state=1, max_iter=500)

In [ ]:
model_application_and_evaluation(scaler1, baseline_regression, X_train, X_test, y_train, y_test)


In [ ]:
model_application_and_evaluation(scaler2, baseline_regression, X_train, X_test, y_train, y_test)


In [ ]:
model_application_and_evaluation(scaler3, baseline_regression, X_train, X_test, y_train, y_test)
